# Анализ пространственных данных. Домашнее задание №2

Мягкий дедлайн: __4 ноября 2020 г. 23:59__

Жесткий дедлайн (со штрафом в _50%_ от количества набранных вами за ДЗ баллов): __5 ноября 2020 г. 08:59__

Визуализация "чего-либо" __без__ выполненного основного задания оценивается в __0 баллов__

ФИО: `Бакулев Владимир Леонидович`

Группа: `DS-12`

In [1]:
import json
import math
from random import uniform

import osmapi as osm
from OSMPythonTools.overpass import overpassQueryBuilder, Overpass
from OSMPythonTools.nominatim import Nominatim
import folium
from folium import plugins
from openrouteservice import client

import requests
import geopandas as gpd
import pandas as pd

from shapely.geometry import Point, Polygon, shape, LineString, mapping
from shapely.ops import cascaded_union

import rtree.index

## Задание №1. Горячая точка (алгоритм - 10 баллов, визуализация - 10 баллов).

Генерируйте рандомные точки на планете Земля до тех пор, пока не попадете на территорию ``Афганистана``

1. Вы можете использовать функции принадлжености точки полигону и расстояния от точки до полигона (в метрах)
2. Предложите не наивный алгоритм поиска (генерировать __напрямую__ точку из полигона границ Афганистана __запрещено__)

Визуализируйте пошагово предложенный алгоритм при помощи ``Folium``

1.1 Поиск полигона Афганистана

In [2]:
api = osm.OsmApi()

ID_RELATION_BOUNDARY_AFGANISTAN = 303427
relation_boundary_af = api.RelationGet(ID_RELATION_BOUNDARY_AFGANISTAN)

array_way_id = []
for _member in relation_boundary_af['member']:
    if _member['type'] == 'way':
        array_way_id.append(_member['ref'])
        
array_ways = []
for _way_id in array_way_id:
    array_ways.append(api.WayGet(_way_id)['nd'])
    
coord_boundary_af = []
for _ways in array_ways:
    for _way in _ways[:1]: # для уменьшения размера полигона берем только первую точку 
        coord = api.NodeGet(_way)
        coord_boundary_af.append([coord['lon'], coord['lat']])

('Connection aborted.', RemoteDisconnected('Remote end closed connection without response'))
('Connection aborted.', RemoteDisconnected('Remote end closed connection without response'))
('Connection aborted.', RemoteDisconnected('Remote end closed connection without response'))
('Connection aborted.', RemoteDisconnected('Remote end closed connection without response'))
('Connection aborted.', RemoteDisconnected('Remote end closed connection without response'))


In [3]:
points_boundary_af = []
for _coord in coord_boundary_af:
    points_boundary_af.append(Point(_coord))

polygon_af = Polygon(points_boundary_af)
centriod_af = polygon_af.centroid.coords[0]

map_afganistan = folium.Map(location=list(reversed(centriod_af)),
                            zoom_start=5,
                           )

folium.GeoJson(polygon_af).add_to(map_afganistan)

map_afganistan

1.2 Попадание в Афганистан

In [4]:
def haversine(lon1, lat1, lon2, lat2):
    RADIUS_EARTH = 6371
    lon1, lat1, lon2, lat2 = map(math.radians, [lon1, lat1, lon2, lat2])
    
    dlon = lon2 - lon1 
    dlat = lat2 - lat1 
    a = math.sin(dlat/2)**2 + math.cos(lat1) * math.cos(lat2) * math.sin(dlon/2)**2
    
    return 2 * math.asin(math.sqrt(a)) * RADIUS_EARTH

In [45]:
def func_random_coord(lon_bound, lat_bound):
    return [uniform(lon_bound[0], lon_bound[1]), uniform(lat_bound[0], lat_bound[1])]

lon_bound_left, lon_bound_right = -180.0, 180.0
lat_bound_left, lat_bound_right = -85.0, 85.0
random_coord = func_random_coord(lon_bound=[lon_bound_left, lon_bound_right], 
                                 lat_bound=[lat_bound_left, lat_bound_right])
array_coord = [random_coord]
random_point = Point(random_coord)

while not random_point.within(polygon_af):
    lon1, lat1 = centriod_af
    lon2, lat2 = random_coord[0], random_coord[1]
    dist = haversine(lon1, lat1, lon2, lat2) / 100

    lon_bound_left, lon_bound_right = centriod_af[0] - dist, centriod_af[0] + dist
    lat_bound_left, lat_bound_right = centriod_af[1] - dist, centriod_af[1] + dist
    
    random_coord = func_random_coord(lon_bound=[lon_bound_left, lon_bound_right], 
                                     lat_bound=[lat_bound_left, lat_bound_right])
    
    array_coord.append(random_coord)
                       
    random_point = Point(random_coord)  

1.3 Отрисовка алгоритма

In [46]:
map_afganistan = folium.Map(location=[0.0, 0.0],
                            tiles='OpenStreetMap',
                            zoom_start=2,
                           )

points_boundary_af = []
for _coord in coord_boundary_af:
    points_boundary_af.append(Point(_coord))

folium.GeoJson(polygon_af).add_to(map_afganistan)

array_coord_revers = []
for _coord in array_coord:
    array_coord_revers.append([_coord[1], _coord[0]])

plane_line = folium.PolyLine(
    array_coord_revers,
    weight=1,
    color='black'
).add_to(map_afganistan)

attr = {'font-weight': 'bold', 'font-size': '24'}

plugins.PolyLineTextPath(
    plane_line,
    '\u2708     ',
    repeat=True,
    offset=8,
    attributes=attr
).add_to(map_afganistan)

AFGANISTAN_POINT = array_coord[-1]
folium.Marker(list(reversed(AFGANISTAN_POINT)), popup='FINISH').add_to(map_afganistan)

map_afganistan

## Задание №2. Качество жизни (20 баллов).

Для измерения показателя качества жизни в точке, найденной в предыдущем задании, вам необходимо рассчитать следующую сумму расстояний (в метрах):

1. Расстояние от точки до 5 ближайших __*__ банкоматов, находящихся в стране с наибольшим количеством объектов жилой недвижимости
2. Расстояние от точки до 5 ближайших школ, находящихся в стране с наибольшим количеством аптек в столице
3. Расстояние от точки до 5 ближайших кинотеатров, наодящихся в стране с самым большим отношением числа железнодорожных станций к автобусным остановкам в южной части __**__

__*__ При поиске _N_ ближайших объектов обязательно использовать ``R-tree``

__**__ Южной частью страны является территория, находящаяся к югу от множества точек, равноудаленных от самой северной и самой южной точек страны

2.1 Поиск стран с id, оканчивающимся на 0

In [47]:
dict_countries = {'county_name': [],
                  'id_country': [], 
                  'id_area': [], 
                 }

overpass = Overpass()
result = overpass.query('relation["admin_level"="2"][boundary=administrative]; out;')

for elem in result.elements():
    if elem.id() % 10 == 0:
        _country = elem.tags()['name:en']
        dict_countries['county_name'].append(_country)
        dict_countries['id_country'].append(elem.id())
        
        if len(_country.split('-')) > 1:
            _country = _country.split('-')[1].strip()
        nominatim = Nominatim()
        dict_countries['id_area'].append(nominatim.query(_country.split('-')).areaId())

countries_df = pd.DataFrame(dict_countries)
countries_df.head(100)

county_name  id_country     id_area
0                     Brazil       59470  3600059470
1                    Estonia       79510  3600079510
2                  Australia       80500  3600080500
3                   Eswatini       88210  3600088210
4        France - Luxembourg       90340  3602171347
5           France - Andorra      126410  3600009407
6                 Bangladesh      184640  3600184640
7                      Syria      184840  3600184840
8                    Liberia      192780  3600192780
9   Central African Republic      192790  3600192790
10                  Ethiopia      192800  3600192800
11                  Cameroon      192830  3600192830
12                  Tanzania      195270  3600195270
13                    Malawi      195290  3600195290
14                Uzbekistan      196240  3600196240
15                  Honduras      287670  3600287670
16                  Portugal      295480  3600295480
17                Azerbaijan      364110  3600364110
18                    Taiwan      449220  3607219605
19                   Comoros      535790  3600535790
20     São Tomé and Príncipe      535880  3600535880
21                 Singapore      536780  3601769123
22       Antigua and Barbuda      536900  3600536900
23                    Kosovo     2088990  3602088990
24                    Brunei     2103120  3602103120
25                   Tokelau     2186600  3602186600
26                    Norway     2978650  3602978650

2.2 Поиск страны с наибольшим колличеством жилой недвижимости

In [48]:
dict_residential = {'id_area': [],
                    'count_residential': []
                   }

for id_area in countries_df['id_area']:  
    overpass = Overpass()
    query = overpassQueryBuilder(area=id_area, 
                                 elementType=['node', 'way', 'relation'], 
                                 selector='"landuse"="residential"', 
                                 out='count')
    result = overpass.query(query, timeout=120)
    count_res = result.countElements()
    dict_residential['id_area'].append(id_area)
    dict_residential['count_residential'].append(count_res)
    
count_residential_df = pd.DataFrame(dict_residential)
countries_1_df = pd.merge(countries_df, count_residential_df, how='outer', on='id_area')
countries_1_df.head(100)

county_name  id_country     id_area  count_residential
0                     Brazil       59470  3600059470              56549
1                    Estonia       79510  3600079510               5145
2                  Australia       80500  3600080500              51232
3                   Eswatini       88210  3600088210                248
4        France - Luxembourg       90340  3602171347               2684
5           France - Andorra      126410  3600009407                 86
6                 Bangladesh      184640  3600184640              49500
7                      Syria      184840  3600184840              15939
8                    Liberia      192780  3600192780              18377
9   Central African Republic      192790  3600192790              16027
10                  Ethiopia      192800  3600192800              62406
11                  Cameroon      192830  3600192830             139056
12                  Tanzania      195270  3600195270             129569
13                    Malawi      195290  3600195290              16901
14                Uzbekistan      196240  3600196240               6312
15                  Honduras      287670  3600287670               1043
16                  Portugal      295480  3600295480              19458
17                Azerbaijan      364110  3600364110               5036
18                    Taiwan      449220  3607219605              10494
19                   Comoros      535790  3600535790                327
20     São Tomé and Príncipe      535880  3600535880                414
21                 Singapore      536780  3601769123               2530
22       Antigua and Barbuda      536900  3600536900                176
23                    Kosovo     2088990  3602088990               1683
24                    Brunei     2103120  3602103120                 89
25                   Tokelau     2186600  3602186600                  4
26                    Norway     2978650  3602978650              16356

In [49]:
countries_1_df.sort_values('count_residential', ascending=False).head()

county_name  id_country     id_area  count_residential
11    Cameroon      192830  3600192830             139056
12    Tanzania      195270  3600195270             129569
10    Ethiopia      192800  3600192800              62406
0       Brazil       59470  3600059470              56549
2    Australia       80500  3600080500              51232

#### Это Камерун!
2.3 Поиск 5 ближайших банкоматов в Камеруне

In [50]:
overpass = Overpass()
query = overpassQueryBuilder(area=3600192830, 
                             elementType=['node', 'way', 'relation'], 
                             selector='"amenity"="atm"', 
                             includeGeometry=True)

result = overpass.query(query, timeout=120)

In [51]:
coordinates_atm = []
idx = rtree.index.Rtree()
for i, elem in enumerate(result.elements()):
    coord = elem.geometry()["coordinates"]
    coordinates_atm.append(coord)
    idx.insert(i, coord)

nearest_atm_idx = list(idx.nearest(AFGANISTAN_POINT, 5))
print('Номера ближайших банкоматов:', nearest_atm_idx)
print('Проверяем по карте (№4 действительно самый ближный)')

m = folium.Map(
    location=[20.0, 40.0],
    zoom_start=4,
)

folium.GeoJson(polygon_af).add_to(m)

for i, _coord in enumerate(coordinates_atm):
    folium.Marker([_coord[1], _coord[0]], tooltip=i).add_to(m)
    
m

Номера ближайших банкоматов: [4, 12, 7, 6, 5]
Проверяем по карте (№4 действительно самый ближный)


In [52]:
sum_dist_atm = 0
for idx in nearest_atm_idx:
    lon, lat = coordinates_atm[idx][0], coordinates_atm[idx][1]
    sum_dist_atm += haversine(lon, lat, AFGANISTAN_POINT[0], AFGANISTAN_POINT[1])
print('Суммарное расстояние до пяти ближайших банкоматов в Камеруне:', round(sum_dist_atm), 'км')

Суммарное расстояние до пяти ближайших банкоматов в Камеруне: 32230 км


2.4 Поиск столиц

In [53]:
dict_capitals = {'id_area': [],
                 'capital': []
                }

for id_area in countries_df['id_area']:  
    overpass = Overpass()
    query = overpassQueryBuilder(area=id_area, 
                                 elementType=['node', 'way', 'relation'], 
                                 selector='"capital"="yes"', 
                                 out='body')
    result = overpass.query(query, timeout=120)
    dict_capitals['id_area'].append(id_area)
    dict_capitals['capital'].append(result)
    
capital_array = []
for cap in dict_capitals['capital']:
    capital_array.append('')
    for ecap in cap.elements():
        capital_array[-1]= ecap.tags()['name:en']
        break

dict_capitals['capital'] = capital_array
    
capitals_df = pd.DataFrame(dict_capitals)
countries_2_df = pd.merge(countries_1_df, capitals_df, how='outer', on='id_area')

# Добираем руками
countries_2_df.loc[20, 'capital'] = 'São Tomé'
countries_2_df.loc[25, 'capital'] = 'Tokelau'

countries_2_df.head(100)

county_name  id_country     id_area  count_residential  \
0                     Brazil       59470  3600059470              56549   
1                    Estonia       79510  3600079510               5145   
2                  Australia       80500  3600080500              51232   
3                   Eswatini       88210  3600088210                248   
4        France - Luxembourg       90340  3602171347               2684   
5           France - Andorra      126410  3600009407                 86   
6                 Bangladesh      184640  3600184640              49500   
7                      Syria      184840  3600184840              15939   
8                    Liberia      192780  3600192780              18377   
9   Central African Republic      192790  3600192790              16027   
10                  Ethiopia      192800  3600192800              62406   
11                  Cameroon      192830  3600192830             139056   
12                  Tanzania      195270  3600195270             129569   
13                    Malawi      195290  3600195290              16901   
14                Uzbekistan      196240  3600196240               6312   
15                  Honduras      287670  3600287670               1043   
16                  Portugal      295480  3600295480              19458   
17                Azerbaijan      364110  3600364110               5036   
18                    Taiwan      449220  3607219605              10494   
19                   Comoros      535790  3600535790                327   
20     São Tomé and Príncipe      535880  3600535880                414   
21                 Singapore      536780  3601769123               2530   
22       Antigua and Barbuda      536900  3600536900                176   
23                    Kosovo     2088990  3602088990               1683   
24                    Brunei     2103120  3602103120                 89   
25                   Tokelau     2186600  3602186600                  4   
26                    Norway     2978650  3602978650              16356   

                capital  
0              Brasília  
1               Tallinn  
2              Canberra  
3               Mbabane  
4            Luxembourg  
5      Andorra la Vella  
6                 Dhaka  
7              Damascus  
8              Monrovia  
9                Bangui  
10          Addis Ababa  
11              Yaounde  
12               Dodoma  
13             Lilongwe  
14             Tashkent  
15          Tegucigalpa  
16               Lisbon  
17                 Baku  
18               Taipei  
19               Moroni  
20             São Tomé  
21            Singapore  
22           St. John's  
23             Pristina  
24  Bandar Seri Begawan  
25              Tokelau  
26                 Oslo

In [54]:
areaId_capital = []
for cap in countries_2_df['capital']:

    nominatim = Nominatim()
    areaId = nominatim.query(cap).areaId()
    areaId_capital.append(str(areaId))
    
countries_2_df['id_area_capital'] = areaId_capital
# Вручную исправляем для Бразилии
countries_2_df.loc[0, 'id_area_capital'] = nominatim.query('RA I').areaId()
# Вручную добавляем
countries_2_df.loc[2, 'id_area_capital'] = nominatim.query('AU-ACT').areaId()
countries_2_df.loc[3, 'id_area_capital'] = nominatim.query('SZ').areaId()
countries_2_df

county_name  id_country     id_area  count_residential  \
0                     Brazil       59470  3600059470              56549   
1                    Estonia       79510  3600079510               5145   
2                  Australia       80500  3600080500              51232   
3                   Eswatini       88210  3600088210                248   
4        France - Luxembourg       90340  3602171347               2684   
5           France - Andorra      126410  3600009407                 86   
6                 Bangladesh      184640  3600184640              49500   
7                      Syria      184840  3600184840              15939   
8                    Liberia      192780  3600192780              18377   
9   Central African Republic      192790  3600192790              16027   
10                  Ethiopia      192800  3600192800              62406   
11                  Cameroon      192830  3600192830             139056   
12                  Tanzania      195270  3600195270             129569   
13                    Malawi      195290  3600195290              16901   
14                Uzbekistan      196240  3600196240               6312   
15                  Honduras      287670  3600287670               1043   
16                  Portugal      295480  3600295480              19458   
17                Azerbaijan      364110  3600364110               5036   
18                    Taiwan      449220  3607219605              10494   
19                   Comoros      535790  3600535790                327   
20     São Tomé and Príncipe      535880  3600535880                414   
21                 Singapore      536780  3601769123               2530   
22       Antigua and Barbuda      536900  3600536900                176   
23                    Kosovo     2088990  3602088990               1683   
24                    Brunei     2103120  3602103120                 89   
25                   Tokelau     2186600  3602186600                  4   
26                    Norway     2978650  3602978650              16356   

                capital id_area_capital  
0              Brasília      3602758138  
1               Tallinn      3602164745  
2              Canberra      3602354197  
3               Mbabane      3600088210  
4            Luxembourg      3602171347  
5      Andorra la Vella      3603657693  
6                 Dhaka      3610249594  
7              Damascus      3600186228  
8              Monrovia      3609319970  
9                Bangui      3607322726  
10          Addis Ababa      3601707699  
11              Yaounde      3602746229  
12               Dodoma      3601600774  
13             Lilongwe      3607345524  
14             Tashkent      3602216724  
15          Tegucigalpa      3603850824  
16               Lisbon      3605400890  
17                 Baku      3603764541  
18               Taipei      3601293250  
19               Moroni      3600198859  
20             São Tomé      3609377730  
21            Singapore      3601769123  
22           St. John's      3602805426  
23             Pristina      3607118787  
24  Bandar Seri Begawan      3608748136  
25              Tokelau      3602186600  
26                 Oslo      3600406091

2.5 Подсчет колличества аптек

In [55]:
dict_pharmacy = {'id_area_capital': [],
                 'count_pharmacy': []
                }

for id_area_capital in countries_2_df['id_area_capital']:
    overpass = Overpass()
    query = overpassQueryBuilder(area=id_area_capital, 
                                 elementType=['node', 'way', 'relation'], 
                                 selector='"amenity"="pharmacy"', 
                                 out='count')
    result = overpass.query(query, timeout=120)
    dict_pharmacy['id_area_capital'].append(id_area_capital)
    dict_pharmacy['count_pharmacy'].append(result.countElements())
    
pharmacy_df = pd.DataFrame(dict_pharmacy)
countries_3_df = pd.merge(countries_2_df, pharmacy_df, how='outer', on='id_area_capital')
countries_3_df.head(100)

county_name  id_country     id_area  count_residential  \
0                     Brazil       59470  3600059470              56549   
1                    Estonia       79510  3600079510               5145   
2                  Australia       80500  3600080500              51232   
3                   Eswatini       88210  3600088210                248   
4        France - Luxembourg       90340  3602171347               2684   
5           France - Andorra      126410  3600009407                 86   
6                 Bangladesh      184640  3600184640              49500   
7                      Syria      184840  3600184840              15939   
8                    Liberia      192780  3600192780              18377   
9   Central African Republic      192790  3600192790              16027   
10                  Ethiopia      192800  3600192800              62406   
11                  Cameroon      192830  3600192830             139056   
12                  Tanzania      195270  3600195270             129569   
13                    Malawi      195290  3600195290              16901   
14                Uzbekistan      196240  3600196240               6312   
15                  Honduras      287670  3600287670               1043   
16                  Portugal      295480  3600295480              19458   
17                Azerbaijan      364110  3600364110               5036   
18                    Taiwan      449220  3607219605              10494   
19                   Comoros      535790  3600535790                327   
20     São Tomé and Príncipe      535880  3600535880                414   
21                 Singapore      536780  3601769123               2530   
22       Antigua and Barbuda      536900  3600536900                176   
23                    Kosovo     2088990  3602088990               1683   
24                    Brunei     2103120  3602103120                 89   
25                   Tokelau     2186600  3602186600                  4   
26                    Norway     2978650  3602978650              16356   

                capital id_area_capital  count_pharmacy  
0              Brasília      3602758138             123  
1               Tallinn      3602164745              82  
2              Canberra      3602354197              46  
3               Mbabane      3600088210              10  
4            Luxembourg      3602171347              99  
5      Andorra la Vella      3603657693              15  
6                 Dhaka      3610249594               0  
7              Damascus      3600186228               2  
8              Monrovia      3609319970               3  
9                Bangui      3607322726               3  
10          Addis Ababa      3601707699             164  
11              Yaounde      3602746229             148  
12               Dodoma      3601600774              20  
13             Lilongwe      3607345524              10  
14             Tashkent      3602216724             853  
15          Tegucigalpa      3603850824             161  
16               Lisbon      3605400890             295  
17                 Baku      3603764541             243  
18               Taipei      3601293250             285  
19               Moroni      3600198859               0  
20             São Tomé      3609377730               0  
21            Singapore      3601769123              85  
22           St. John's      3602805426              14  
23             Pristina      3607118787              75  
24  Bandar Seri Begawan      3608748136               4  
25              Tokelau      3602186600               0  
26                 Oslo      3600406091             129

In [56]:
countries_3_df.sort_values('count_pharmacy', ascending=False).head()

county_name  id_country     id_area  count_residential      capital  \
14  Uzbekistan      196240  3600196240               6312     Tashkent   
16    Portugal      295480  3600295480              19458       Lisbon   
18      Taiwan      449220  3607219605              10494       Taipei   
17  Azerbaijan      364110  3600364110               5036         Baku   
10    Ethiopia      192800  3600192800              62406  Addis Ababa   

   id_area_capital  count_pharmacy  
14      3602216724             853  
16      3605400890             295  
18      3601293250             285  
17      3603764541             243  
10      3601707699             164

#### Это Ташкент!

2.6 Поиск 5 ближайших школ в Ташкенте к точке в Афганистане 

In [57]:
overpass = Overpass()
query = overpassQueryBuilder(area=3602216724, 
                             elementType=['node', 'way', 'relation'], 
                             selector='"amenity"="school"', 
                             includeGeometry=True)

result = overpass.query(query, timeout=120)

In [58]:
coordinates_school = []
idx = rtree.index.Rtree()
for i, elem in enumerate(result.elements()):
    coord = elem.geometry()["coordinates"]
    if i > 100: # смотрим первые сто школ
        break

    coordinates_school.append(coord)
    idx.insert(i, coord)

nearest_school_idx = list(idx.nearest(AFGANISTAN_POINT, 5))
print('Номера ближайших школ:', nearest_school_idx)

m = folium.Map(
    location=[40.0, 70.0],
    zoom_start=7,
)

folium.GeoJson(polygon_af).add_to(m)

for i, _coord in enumerate(coordinates_school):
    folium.Marker([_coord[1], _coord[0]], tooltip=i).add_to(m)
    
m

Номера ближайших школ: [3, 100, 82, 30, 79]


In [59]:
sum_dist_school = 0
for idx in nearest_school_idx:
    lon, lat = coordinates_school[idx][0], coordinates_school[idx][1]
    sum_dist_school += haversine(lon, lat, AFGANISTAN_POINT[0], AFGANISTAN_POINT[1])
print('Суммарное расстояние до пяти ближайших школ в Ташкенте:', round(sum_dist_school), 'км')

Суммарное расстояние до пяти ближайших школ в Ташкенте: 3006 км


In [60]:
print('Общая сумма (без учета п.2.3): ', round(sum_dist_atm + sum_dist_school), 'км')

Общая сумма (без учета п.2.3):  35236 км


## Задание №3. Поездка по Нью-Йорку (маршрут - 20 баллов, визуализация - 10 баллов).

Добраться __на автомобиле__ от входа в ``Central Park`` __Нью-Йорка__ (со стороны ``5th Avenue``) до пересечения ``Water Street`` и ``Washington Street`` в Бруклине (откуда получаются лучшие фото Манхэттенского моста) довольно непросто - разумеется, из-за вечных пробок. Однако еще сложнее это сделать, проезжая мимо школ, где дети то и дело переходят дорогу в неположенном месте.

Вам необходимо построить описанный выше маршрут, избегая на своем пути школы. Визуализируйте данный маршрут (также добавив школы и недоступные для проезда участки дорог) при помощи ``Folium``

Данные о расположении школ Нью-Йорка можно найти [здесь](https://catalog.data.gov/dataset/2019-2020-school-point-locations)

3.1 Отрисовка обычного маршрута

In [61]:
START = [40.7655, -73.9731]
FINISH = [40.70319, -73.98959]

REV_START = [START[1], START[0]]
REV_FINISH = [FINISH[1], FINISH[0]]

In [62]:
def style_function(color):
    return lambda feature: dict(color=color,
                                opacity=0.5,
                                weight=4,)

In [63]:
api_key = '5b3ce3597851110001cf62486fd5492c63f243679663e76efb94dc47' 
clnt = client.Client(key=api_key)

INIT_ZOOM = [40.7398, -73.9832]
map_newyork = folium.Map(location=INIT_ZOOM, 
                         zoom_start=13)

popup_route = "<h4>{0} route</h4><hr>" \
             "<strong>Duration: </strong>{1:.1f} mins<br>" \
             "<strong>Distance: </strong>{2:.1f} km" 

coordinates = [REV_START, REV_FINISH]
direction_params = {'coordinates': coordinates,
                    'profile': 'driving-car', 
                    'format_out': 'geojson',
                    'preference': 'shortest',
                    'geometry': 'true'}

regular_route = clnt.directions(**direction_params)

duration, distance = regular_route['features'][0]['properties']['summary'].values()
popup = folium.map.Popup(popup_route.format('Regular', 
                                            duration / 60, 
                                            distance / 1000))

gj= folium.GeoJson(regular_route,
                   name='Regular Route',
                   style_function=style_function('blue')).add_child(popup).add_to(map_newyork)

folium.Marker(list(reversed(coordinates[0])), popup='Central Park').add_to(map_newyork)
folium.Marker(list(reversed(coordinates[1])), popup='Water Street & Washington Street').add_to(map_newyork)

map_newyork

3.2 Отрисовка школ

In [64]:
r = requests.get("https://data.cityofnewyork.us/api/views/a3nt-yts4/rows.json")
r.raise_for_status()

In [65]:
data_school = r.json()
array_coord_school = []
for _school in data_school['data']:
    for _s in _school:
        if 'POINT' in str(_s):
            _s = _s.split()[1:]
            array_coord_school.append([float(_s[0][1:]), float(_s[1][:-1])])

Оставляем только те школы, которые могут встреться у нас на маршруте

In [66]:
eps_x, eps_y = 1e-1, 1e-1
p1 = Point([INIT_ZOOM[1] - eps_x, INIT_ZOOM[0] - eps_y])
p2 = Point([INIT_ZOOM[1] - eps_x, INIT_ZOOM[0] + eps_y])
p3 = Point([INIT_ZOOM[1] + eps_x, INIT_ZOOM[0] - eps_y])
p4 = Point([INIT_ZOOM[1] + eps_x, INIT_ZOOM[0] + eps_y])
bound_school = Polygon([p1, p2, p4, p3])

map_newyork_scool_bound = folium.Map(location=INIT_ZOOM, 
                         zoom_start=11)

array_coord_school_in_bound = []
for _school in array_coord_school:
    p = Point(_school)
    if not p.within(bound_school):
        folium.CircleMarker(
        location=[_school[1], _school[0]],
        radius=2,
        color='green',
        fill=True,
        fill_color='#3186cc').add_to(map_newyork_scool_bound )
    else:
        array_coord_school_in_bound.append(_school)
        folium.CircleMarker(
        location=[_school[1], _school[0]],
        radius=2,
        color='red',
        fill=True,
        fill_color='#3186cc').add_to(map_newyork_scool_bound )

folium.GeoJson(bound_school).add_to(map_newyork_scool_bound )

map_newyork_scool_bound 

In [67]:
map_newyork_scool = folium.Map(location=INIT_ZOOM, 
                         zoom_start=13)

polygons_school = []
for coord in array_coord_school_in_bound:
    eps = 5e-4
    p1 = Point([coord[0] - eps, coord[1] - eps])
    p11 = Point([coord[0] - 1.8 * eps, coord[1]])
    p2 = Point([coord[0] - eps, coord[1] + eps])
    p3 = Point([coord[0] + eps, coord[1] - eps])
    p33 = Point([coord[0] + 1.8 * eps, coord[1]])
    p4 = Point([coord[0] + eps, coord[1] + eps])
    poly = Polygon([p1, p11, p2, p4, p33, p3])
    polygons_school.append(poly)
    folium.GeoJson(poly).add_to(map_newyork_scool)

union_school = cascaded_union(polygons_school)  
map_newyork_scool

In [68]:
school_request = {'coordinates': coordinates, 
                'format_out': 'geojson',
                'profile': 'driving-car',
                'preference': 'shortest',
                'instructions': False,
                 'options': {'avoid_polygons': mapping(union_school)}} 
route_school = clnt.directions(**school_request)

distance, duration = route_school['features'][0]['properties']['summary'].values()
popup = folium.map.Popup(popup_route.format('Diesel Route',
                                                 duration/60,
                                                 distance/1000))

folium.GeoJson(route_school,
               style_function=style_function('black'), 
               name='Route after Jan 2019').add_child(popup).add_to(map_newyork_scool)

map_newyork_scool.add_child(folium.map.LayerControl())